# Import Libraries

In [1]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import matplotlib.pyplot as plt
import keras
from keras.models import Sequential
from keras.layers import Dense,Conv2D,Flatten,MaxPool2D,Dropout
import wandb
from wandb.keras import WandbCallback

# Initialize Variables

In [2]:
target_size = (75,75)
batch_size = 32
train_val_split = 0.2
num_classes = 45
nb_epochs = 1000
init_epoch = 29
wandb_resume_state = True
exp_name = 'pfd9f98m'

In [3]:
wandb.login(key='xxxxxxxxxxxxx')

wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [4]:
if wandb_resume_state:
    wandb.init(project="Fashion-Classification", resume=True, group=exp_name)
else:    
    exp_name = wandb.util.generate_id()
    myrun = wandb.init(
            project='Fashion-Classification',
            group=exp_name,
            config={
                'Image Size':75,
                'Num Channels':3,
                'Epoch': nb_epochs,
                'Batch_size':batch_size,
                'Loss':"categorical_crossentropy",            
                'Optimizer':'Adam',
            }
    )
config = wandb.config
print(exp_name)

wandb: Currently logged in as: avinash-218. Use `wandb login --relogin` to force relogin


pfd9f98m


# Data Generator

In [5]:
train_data_gen = ImageDataGenerator(rescale=1./255, validation_split=train_val_split)

train_generator = train_data_gen.flow_from_directory(
    directory='../input/fashioncategorized',
    target_size = target_size,
    batch_size = batch_size,
    #color_mode='grayscale',
    class_mode = 'categorical',
    subset='training')

validation_generator = train_data_gen.flow_from_directory(
    directory='../input/fashioncategorized',
    target_size = target_size,
    batch_size = batch_size,
    #color_mode='grayscale',
    class_mode = 'categorical',
    subset='validation')

Found 35557 images belonging to 45 classes.


Found 8862 images belonging to 45 classes.


In [6]:
labels = list(train_generator.class_indices.keys())

# Model

In [7]:
if wandb.run.resumed: #if run is to be resumed
    model = keras.models.load_model(wandb.restore("model-best.h5").name)
else:#else new run
    model= Sequential()
    model.add(Conv2D(kernel_size=(3,3), filters=32, activation='tanh', input_shape=(75,75,3)))
    model.add(Conv2D(filters=30,kernel_size = (3,3),activation='tanh'))
    model.add(MaxPool2D(2,2))
    model.add(Conv2D(filters=30,kernel_size = (3,3),activation='tanh'))
    model.add(MaxPool2D(2,2))
    model.add(Conv2D(filters=30,kernel_size = (3,3),activation='tanh'))

    model.add(Flatten())

    model.add(Dense(20,activation='relu'))
    model.add(Dense(15,activation='relu'))
    model.add(Dense(num_classes,activation = 'softmax'))

model.compile(loss='categorical_crossentropy', metrics=['acc'], optimizer='adam')

2022-06-13 18:37:40.783909: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-06-13 18:37:40.894392: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-06-13 18:37:40.895170: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero


2022-06-13 18:37:40.897562: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-06-13 18:37:40.897890: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-06-13 18:37:40.898659: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-06-13 18:37:40.899342: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA 

In [8]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 73, 73, 32)        896       
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 71, 71, 30)        8670      
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 35, 35, 30)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 33, 33, 30)        8130      
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 16, 16, 30)        0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 14, 14, 30)        8130      
_________________________________________________________________
flatten (Flatten)            (None, 5880)              0

# Fit

In [9]:
#wandb keras compatibility
wandb_call = WandbCallback(save_model=True,
                          save_graph=True,
                          save_weights_only=True,
                          log_weights=True,
                          log_gradients=True,
                          training_data=train_generator,
                          validation_data=validation_generator,
                          validation_steps = validation_generator.samples // batch_size,
                          labels=labels,
                          predictions = 180,
                          input_type='images')

wandb: WARNING The save_model argument by default saves the model in the HDF5 format that cannot save custom objects like subclassed models and custom layers. This behavior will be deprecated in a future release in favor of the SavedModel format. Meanwhile, the HDF5 model is saved as W&B files and the SavedModel as W&B Artifacts.


In [10]:
history = model.fit(
    train_generator,
    initial_epoch=wandb.run.step,
    steps_per_epoch = train_generator.samples // batch_size,
    validation_data = validation_generator, 
    validation_steps = validation_generator.samples // batch_size,
    epochs = nb_epochs,
    callbacks=[wandb_call])

2022-06-13 18:37:45.523388: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


Epoch 1/1000


2022-06-13 18:37:48.532944: I tensorflow/stream_executor/cuda/cuda_dnn.cc:369] Loaded cuDNN version 8005



   1/1111 [..............................] - ETA: 2:52:21 - loss: 3.8249 - acc: 0.0000e+00


   3/1111 [..............................] - ETA: 13:04 - loss: 3.6934 - acc: 0.0000e+00  

...


 920/1111 [=======================>......] - ETA: 3:20 - loss: 0.0667 - acc: 0.9783


 921/1111 [=======================>......] - ETA: 3:19 - loss: 0.0666 - acc: 0.9783


 922/1111 [=======================>......] - ETA: 3:18 - loss: 0.0667 - acc: 0.9783


 923/1111 [=======================>......] - ETA: 3:17 - loss: 0.0667 - acc: 0.9783


 924/1111 [=======================>......] - ETA: 3:16 - loss: 0.0666 - acc: 0.9783